In [86]:
import datetime 
from datetime import datetime
from enum import Enum
import math
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import PSpincalc as sp
import socket as soc
from socket import timeout
import struct
import subprocess
import sys
from time import sleep


# code to speed test


class Socket_struct:
    pass

class Socket_info:
    pass

class Bone_struct:
    pass

class Settings:
    pass

class UDP_Settings:
    pass

UDP_sett = UDP_Settings()

sett = Settings()


##################      MODE      ##################


class Mode_enum(Enum):
    custom = 0
    avatar = 1
    acquisition = 2
    control = 3
    
##################      CONSTANTS      ##################
        
# size of the BONE structure
BONE_S_SIZE = 8

# number of bones in skeleton
N_RB_IN_SKEL = 21

AXIS = {0 : 'roll', 1 : 'pitch'}
PHASE_ROLL = {0 : 'straight', 1 : 'up', 2 : 'down'}
PHASE_PITCH = {0 : 'straight', 1 : 'right', 2 : 'left'}

PHASE = {'roll' : PHASE_ROLL, 'pitch' : PHASE_ROLL}

##################      FUNCTIONS      ##################


def setup(IP, PORT, ID, timeout = 0.1):
    # Datagram (udp) socket
    try:
        socket = soc.socket(soc.AF_INET, soc.SOCK_DGRAM)
        print('socket ', ID, ' created')
    except socket.error as msg:
        print('Failed to create socket. Error : ', msg)
        sys.exit()
    # Bind socket to local IP and port
    try:
        socket.bind((IP, PORT))
    except soc.error as msg:
        print('Bind failed. Error Code : ', msg)
        sys.exit()
    print('socket ', ID, ' bind complete')

    # set timeout
    socket.settimeout(timeout)

    read_s = Socket_struct() # Create an empty socket structure

    read_s.socket = socket
    read_s.ID = ID

    return read_s


def udp_read(Read_struct):
    # print('\nREADING FROM', Read_struct.type, '\n')
    # receive data from client (data, addr)

    try:
        data, addr = Read_struct.socket.recvfrom(4096)
    except timeout:
        
        if sett.DUMMY_READ:
            if Read_struct.ID == 'MOTIVE_SK':
                data = []
                one_rb = b'\x01\x00\x04\x00\xd0hG?\xe7sp?.\xbf\x93\xc0\\f\xbf=$\xd9j?]\xa9\x94=~\x92\xc2>'
                for i in range(21):
                    data = data + one_rb if len(data) else one_rb
            else:
                return 't'
        else:
            return 't'
        
    return data

def udp_process(data, Read_struct):

    if data == 't':
        return 't'
    
    if Read_struct.ID == 'MOTIVE_RB':

        if not data:
            return None

        # print("Byte Length of Message :", len(data), "\n")
        strs = ""

        # THIS IS A int_32

        for i in range(0, 1):
            strs += "i"

        # THIS IS A float

        for i in range(1, len(data) // 4):
            strs += "f"

        # print(strs)

        # print("Message Data (skeletal bone):", struct.unpack(strs, data), "\n")

        data_ump = struct.unpack(strs, data)

        bone_s = Bone_struct()
    #         print(int(bin(data[0])[-8:], 2))
        bone_s.ID = int(bin(data_ump[0])[-8:], 2)
        bone_s.position = data_ump[1:4]
        quaternion_t = data_ump[4:]
        order = [3, 0, 1, 2]

        bone_s.quaternion = [quaternion_t[i] for i in order]

        # print(bone_s.quaternion)
        bone_s.euler = sp.Q2EA(np.array(bone_s.quaternion), EulerOrder="zyx", ignoreAllChk=True)[0]

    elif Read_struct.ID == 'MOTIVE_SK':

        if not data:
            return None

        # print("Byte Length of Message :", len(data), "\n")
        strs = ""

        # one int and 7 floats, '21' times

        for i in range(0, len(data) // 4):
            if i % 8 == 0:
                strs += "i"
            else:
                strs += "f"

        # print("Message Data (skeletal bone):", struct.unpack(strs, data), "\n")

        data_ump = struct.unpack(strs, data)

        Q_ORDER = [3, 0, 1, 2]

        for i in range(0, len(data_ump) // BONE_S_SIZE):
            bone = list(data_ump[i*BONE_S_SIZE : (1+i)*BONE_S_SIZE])

            # print bone


            if i == 0:
                ID = [(int(bin(bone[0])[-8:], 2))]
                position = np.array(bone[1:4])
                quaternion_t = np.array(bone[4:])
                quaternion = np.array([quaternion_t[j] for j in Q_ORDER])
                euler = sp.Q2EA(np.array(quaternion), EulerOrder="zyx", ignoreAllChk=True)[0]
            else:
                ID = ID + [(int(bin(bone[0])[-8:], 2))]
                position = np.vstack((position, bone[1:4]))
                quaternion_t = bone[4:]
                quaternion = np.vstack((quaternion, [quaternion_t[j] for j in Q_ORDER]))
                euler = np.vstack((euler, (sp.Q2EA(np.array(quaternion), EulerOrder="zyx", ignoreAllChk=True)[0])))
            
        ID = np.array(ID)
        
        data = np.c_[ID, position, quaternion, euler]
        
        # sort by ID
        data = data[data[:, 0].argsort()]

        return data

    elif Read_struct.ID == 'UNITY_CALIB':

        if not data:
            return None

#         print("Byte Length of Message :", len(data), "\n")
        strs = ""
        for i in range(0, len(data)//4):
            strs += "f"

        # print(strs)
        # print(len(data))

        unity_control = struct.unpack(strs, data)
        # print("Message Data :", unity_control, "\n")
        return unity_control

    elif Read_struct.ID == 'UNITY_INFO':

        if not data:
            return None

#         print("Byte Length of Message :", len(data), "\n")
        strs = ""
        for i in range(0, len(data)//4):
            strs += "i"

        # print(strs)
        # print(len(data))

        unity_info = struct.unpack(strs, data)
        # print("Message Data :", unity_control, "\n")
        return unity_info

    elif Read_struct.ID == 'UNITY_QUERY':

        if not data:
            return None

        # we receive a char

        unity_query = data.decode("utf-8") 
#         print("Message Data :", unity_query, "\n")
        return unity_query


def write(Write_struct, towhom, msg):
    Write_struct.socket.sendto(msg, (towhom.IP, towhom.PORT))
    # print('Sent', msg, towhom.IP, 'port', towhom.PORT)
    return

def read_rb_motive(UDP_sett):

    data = read(Read_motive)

    # ID = np.array(data.ID)
    # pos = np.array(data.position)
    # quat = np.array(data.quaternion)
    # euler = np.array(data.euler)

    # bone = np.append(ID, pos)
    # bone = np.append(bone, quat)
    # bone = np.append(bone, euler)

    # if i>1:
    #     bone_all = np.vstack((bone, bone_old))
    # else:
    #     bone_all = bone

    # bone_old = bone

    # # print (bone)
    # # print (bone_all)

    # motive_data = np.vstack((motive_data, bone))

    # motive_data_full_temp = [s + '_' for s in motive_indices]
    # motive_data_full_temp = [s + str(ID) for s in motive_data_full_temp]

    # motive_data_full = np.append(motive_data_full, motive_data_full_temp)

    # print(motive_data_full)

    return bone


def write_sk_to_unity(Write_unity_sk, client, skel):

    skel_msg = np.reshape(skel[: , :-3], 21 * 8)
    arr = skel_msg.tolist()

    arr = arr + [float(count)]

    strs = ""
    # one int and 7 floats, '21' times

    for i in range(0, len(arr) // 4):
        if i % 8 == 0:
            strs += "i"
        else:
            strs += "f"

    print(arr)
    # print(len(arr))
    message = struct.pack('%sf' % len(arr), *arr)

    # print(message)
    write(Write_unity_sk, client, message)

    if 0:
        plt.axis()
        plt.scatter(count, arr[8*2+1], c = 1)
        plt.pause(0.0001)


In [89]:

##################      SETTINGS      ##################


mode = Mode_enum(2)

filename = datetime.now().strftime("%Y_%b_%d_%I_%M_%S%p")
foldername = 'acquired_data'


sett.N_READS = 100

sett.READ_MOTIVE_RB = 0
sett.READ_MOTIVE_SK = 0
sett.READ_XSENS = 0
sett.READ_FROM_UNITY = 0
sett.READ_QUERY_FROM_UNITY = 0

sett.WRITE_SK_TO_UNITY = 0

sett.OPEN_CLOSE_CONTINUOUS = 0

sett.DUMMY_READ = False

# MOTIVE

UDP_sett.IP_MOTIVE = "127.0.0.1"   # Local MOTIVE client
UDP_sett.PORT_MOTIVE = 9000    # Arbitrary non-privileged port

#UNITY

UDP_sett.IP_UNITY = "127.0.0.1"

UDP_sett.PORT_UNITY_QUERY = 30011

UDP_sett.PORT_UNITY_READ_CALIB = 30012
UDP_sett.PORT_UNITY_READ_CALIB_INFO = 30013


UDP_sett.PORT_UNITY_WRITE_SK = 30000

UDP_sett.PORT_UNITY_WRITE_SK_CLIENT = 26000


if mode.name=='avatar':

    sett.N_READS = 1000

    sett.READ_MOTIVE_SK = 1

    sett.READ_QUERY_FROM_UNITY = 1

    sett.WRITE_SK_TO_UNITY = 1

    sett.OPEN_CLOSE_CONTINUOUS = 1

    sett.DUMMY_READ = False


if mode.name=='acquisition':

    sett.N_READS = math.inf

    sett.READ_MOTIVE_SK = 1

    sett.READ_QUERY_FROM_UNITY = 1

    sett.WRITE_SK_TO_UNITY = 1

    sett.OPEN_CLOSE_CONTINUOUS = 1

    sett.DUMMY_READ = True

In [95]:

##################      IMPLEMENTATION      ##################


start = datetime.now()


if sett.WRITE_SK_TO_UNITY:
    unity_sk_client = Socket_info()

    unity_sk_client.IP = UDP_sett.IP_UNITY
    unity_sk_client.PORT = UDP_sett.PORT_UNITY_WRITE_SK_CLIENT

count = 0

query = ''

# define data structure and headers

        
motive_indices = np.array([])

motive_indices_base = np.char.array([ 'ID', 'pos_x', 'pos_y', 'pos_z', 'quat_x', 'quat_y', 'quat_z', 'quat_w', 'yaw', 'pitch', 'roll' ])

for i in range(N_RB_IN_SKEL):

    n = np.char.array([('_' + str(i))])

    if i==0:
        motive_indices = motive_indices_base + n
    else:
        motive_indices = np.r_[motive_indices, motive_indices_base + n]


unity_indices_calib = np.char.array([ 'Joy 1', 'Joy 2', 'Joy 3', 'Joy 4', 'roll', 'pitch', 'yaw', 'roll_rate', 'pitch_rate', 'yaw_rate', 'vel_x', 'vel_y', 'vel_z', 'vel_semiloc_x', 'vel_semiloc_y', 'vel_semiloc_z', 'corr_roll', 'corr_pitch', 'pos_x', 'pos_y', 'pos_z', 'rot_x', 'rot_y', 'rot_z', 'rot_w', 'timestamp' ])
unity_indices_info = np.char.array([ 'calib_axis', 'calib_phase', 'is_input_not_zero', 'instance', 'loop counter' ])

motive_data = np.array(motive_indices)
unity_data_calib = np.array(unity_indices_calib)
unity_data_info = np.array(unity_indices_info)
calib_data = np.r_[motive_indices, unity_indices_calib, unity_indices_info]

data = calib_data
data = data.reshape(1, data.size)

data_num = np.array([])

# create unity read query / write skeleton socket
Read_unity_query = setup(UDP_sett.IP_UNITY, UDP_sett.PORT_UNITY_QUERY, 'UNITY_QUERY', timeout = 0.001)
Write_unity_sk = Read_unity_query

# create unity control read socket
Read_unity_control = setup(UDP_sett.IP_UNITY, UDP_sett.PORT_UNITY_READ_CALIB, 'UNITY_CALIB',  timeout = 0.001)

# create unity info read socket
Read_unity_info = setup(UDP_sett.IP_UNITY, UDP_sett.PORT_UNITY_READ_CALIB_INFO, 'UNITY_INFO',  timeout = 0.001)

# create motive read socket
Read_motive_sk = setup(UDP_sett.IP_MOTIVE, UDP_sett.PORT_MOTIVE, 'MOTIVE_SK',  timeout = 0.001)
    
while count<sett.N_READS:
    if mode.name=='avatar':

        while count<sett.N_READS:
            # create motive read socket
            # update skeleton
            # close motive read socket
            (skel) = read_sk_motive(UDP_sett)

            query = ''

            # check if unity query
            unity_query = read(Read_unity_query)

            # close unity read socket
            # Write_unity_sk.socket.close()

            # if query : send skeleton
            if unity_query=='r':

                print('sending skeleton to UNITY')

                # send skeleton
                write_sk_to_unity(Write_unity_sk, unity_sk_client, skel)

            elif unity_query=='q':

                # close unity write socket
                Read_unity_query.socket.close()

                break

    elif mode.name=='acquisition':
        
        startloop = datetime.now()

        # consume skeleton
        udp_data = udp_read(Read_motive_sk)
                        
#         print('skeleton = ', udp_data)
        
        timesk = datetime.now();
        print ('time to read and process skeleton =', timesk - startloop)

        query = ''
        
        # read query
        udp_data = udp_read(Read_unity_query)
        unity_query = udp_process(udp_data, Read_unity_query)
             
        print ('UNITY query = ', unity_query)

        timequ = datetime.now();
        print ('time to read query =', timequ - timesk)
        
        # if query : read unity and skeleton, then save to csv
        if unity_query=='a':

            print('saving data to csv')

            # read unity controls and sensors
        
            # read unity control
            udp_data = udp_read(Read_unity_control)
            unity_calib = np.array(udp_process(udp_data, Read_unity_control))
                            
#             print('unity_calib = ', unity_calib)
            
            # read unity info
            udp_data = udp_read(Read_unity_info)
            unity_calib_info = np.array(udp_process(udp_data, Read_unity_info))
                            
            print('unity_calib_info = ', unity_calib_info)
            
            timeun = datetime.now();
            print ('time to read UNITY data =', timeun - timequ)
            
            
            # update skeleton

            # read skeleton
            udp_data = udp_read(Read_motive_sk)
            
            timesk = datetime.now();
            print ('time to read second skeleton =', timesk - timeun)

            skel = udp_process(udp_data, Read_motive_sk)
            
            timesk2 = datetime.now();
            print ('time to process second skeleton =', timesk2 - timesk)
            
            # reshape all to 1D array
            skel = skel.reshape(1, skel.size)
            unity_calib = unity_calib.reshape(1, unity_calib.size)
            unity_calib_info = unity_calib_info.reshape(1, unity_calib_info.size)

#             print(skel.size)
#             print(unity_calib.size)
#             print(unity_calib_info.size)
            
            data_row = np.c_[skel, unity_calib, unity_calib_info]
            
            if data_num.size:
                if data_row.shape[1] == data_num.shape[1]:
                    data_num = np.vstack([data_num, data_row])
                else:
                    print('lost frame')
            else:
                data_num =  data_row
                
                
        elif unity_query=='q':

            # close unity write socket
            Read_unity_query.socket.close()
            
            # close unity control read socket
            Read_unity_control.socket.close()

            # close unity info read socket
            Read_unity_info.socket.close()
            
            # close motive read socket
            Read_motive_sk.socket.close()

            break

    if mode.name=='control':
        
        while True:
            # create motive read socket
            # update skeleton
            # close motive read socket
            (skel, skel_all) = read_sk_motive(sett, UDP_sett, skel_all)

            query = ''

            # check if unity query
            unity_query = read(Read_unity_query)

            # close unity read socket
            # Write_unity_sk.socket.close()

            # if query : send skeleton
            if unity_query=='r':

                print('sending skeleton to UNITY')

                # process skeleton (TOBEDONE)

                # send commands to unity (TOBEDONE)

            elif unity_query=='q':

                # close unity write socket
                Write_unity_sk.socket.close()

                break
            
    count = count + 1



socket  UNITY_QUERY  created
socket  UNITY_QUERY  bind complete
socket  UNITY_CALIB  created
socket  UNITY_CALIB  bind complete
socket  UNITY_INFO  created
socket  UNITY_INFO  bind complete
socket  MOTIVE_SK  created
socket  MOTIVE_SK  bind complete
time to read and process skeleton = 0:00:00.001003
UNITY query =  t
time to read query = 0:00:00.001499
time to read and process skeleton = 0:00:00.001003
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.001502
UNITY query =  t
time to read query = 0:00:00.001031
time to read and process skeleton = 0:00:00.001013
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001005
UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001502
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.002001
UNITY query =  t
time to read query = 0:00:00.001502
time to read and proce

UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001505
UNITY query =  t
time to read query = 0:00:00.001995
time to read and process skeleton = 0:00:00.001995
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.001001
UNITY query =  t
time to read query = 0:00:00.001499
time to read and process skeleton = 0:00:00.001001
UNITY query =  t
time to read query = 0:00:00.001006
time to read and process skeleton = 0:00:00.001503
UNITY query =  t
time to read query = 0:00:00.002000
time to read and process skeleton = 0:00:00.001501
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.001502
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001001
UNITY query =  t
time to read query = 0:00:00.001002
time to read and process skeleton = 0:00:00.002000
UNITY query =  t
time to read query = 0:00:00.001500
time to rea

UNITY query =  t
time to read query = 0:00:00.002001
time to read and process skeleton = 0:00:00.001009
UNITY query =  t
time to read query = 0:00:00.001509
time to read and process skeleton = 0:00:00.001004
UNITY query =  t
time to read query = 0:00:00.001502
time to read and process skeleton = 0:00:00.001006
UNITY query =  t
time to read query = 0:00:00.002009
time to read and process skeleton = 0:00:00.001494
UNITY query =  t
time to read query = 0:00:00.002501
time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001004
UNITY query =  t
time to read query = 0:00:00.002000
time to read and process skeleton = 0:00:00.001500
UNITY query =  t
time to read query = 0:00:00.002001
time to read and process skeleton = 0:00:00.001496
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001029
UNITY query =  t
time to read query = 0:00:00.001975
time to rea

UNITY query =  t
time to read query = 0:00:00.001489
time to read and process skeleton = 0:00:00.001005
UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.001497
time to read and process skeleton = 0:00:00.001501
UNITY query =  t
time to read query = 0:00:00.001008
time to read and process skeleton = 0:00:00.001499
UNITY query =  t
time to read query = 0:00:00.001014
time to read and process skeleton = 0:00:00.001513
UNITY query =  t
time to read query = 0:00:00.001487
time to read and process skeleton = 0:00:00.001488
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.001001
UNITY query =  t
time to read query = 0:00:00.001000
time to read and process skeleton = 0:00:00.001502
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001500
UNITY query =  t
time to read query = 0:00:00.001002
time to rea

time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.002003
time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001001
UNITY query =  t
time to read query = 0:00:00.001008
time to read and process skeleton = 0:00:00.001482
UNITY query =  t
time to read query = 0:00:00.001002
time to read and process skeleton = 0:00:00.001515
UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001488
UNITY query =  t
time to read query = 0:00:00.001499
time to read and process skeleton = 0:00:00.001002
UNITY query =  t
time to read query = 0:00:00.001501
time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001000
UNITY query =  t
time to read query = 0:00:00.001001
time to read and process skeleton = 0:00:00.001002
UNITY query =

...

time to read and process skeleton = 0:00:00.001501
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002002
time to read second skeleton = 0:00:00.001012
time to process second skeleton = 0:00:00.003001
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002002
time to read second skeleton = 0:00:00.001000
time to process second skeleton = 0:00:00.002503
lost frame
time to read and process skeleton = 0:00:00.001495
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002000
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:00:00.002993
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to

unity_calib_info =  t
time to read UNITY data = 0:00:00.002501
time to read second skeleton = 0:00:00.001502
time to process second skeleton = 0:00:00.003992
lost frame
time to read and process skeleton = 0:00:00.001000
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002016
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:00:00.003998
lost frame
time to read and process skeleton = 0:00:00.001510
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002501
time to read second skeleton = 0:00:00.001006
time to process second skeleton = 0:00:00.003988
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.003001
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:

unity_calib_info =  t
time to read UNITY data = 0:00:00.002477
time to read second skeleton = 0:00:00.001486
time to process second skeleton = 0:00:00.004502
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002001
time to read second skeleton = 0:00:00.001502
time to process second skeleton = 0:00:00.004002
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002001
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:00:00.003002
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002502
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:

unity_calib_info =  t
time to read UNITY data = 0:00:00.003001
time to read second skeleton = 0:00:00.001477
time to process second skeleton = 0:00:00.004003
lost frame
time to read and process skeleton = 0:00:00.001016
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002001
time to read second skeleton = 0:00:00.001501
time to process second skeleton = 0:00:00.004003
lost frame
time to read and process skeleton = 0:00:00.001009
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002502
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:00:00.004003
lost frame
time to read and process skeleton = 0:00:00.001501
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002502
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:

time to process second skeleton = 0:00:00.003985
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002501
time to read second skeleton = 0:00:00.001001
time to process second skeleton = 0:00:00.003988
lost frame
time to read and process skeleton = 0:00:00.001015
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002987
time to read second skeleton = 0:00:00.001016
time to process second skeleton = 0:00:00.004002
lost frame
time to read and process skeleton = 0:00:00.001500
UNITY query =  a
time to read query = 0:00:00
saving data to csv
unity_calib_info =  t
time to read UNITY data = 0:00:00.002502
time to read second skeleton = 0:00:00.001489
time to process second skeleton = 0:00:00.003001
lost frame
time to read and process skeleton = 0:00:00.001001
UNITY query =  a
time to read quer

In [96]:
Read_unity_query.socket.close()

data = np.vstack([data, data_num]) if data_num.size else data

# if READ_XSENS:
#     subprocess.Popen(["C:\Users\matteoPC\Documents\GitHub\Python_acquisition\StreamFromXSENS/release/StreamFromXSENS.exe"])


#     start_iter = datetime.now()

#     end_iter = datetime.now()

#     print('iter time = ', end_iter - start_iter)


if not os.path.isdir(foldername):
    os.mkdir(foldername)
    
home_fol = os.getcwd()
os.chdir(foldername)

if data_num.shape[0]>1 and data_num.shape[1]>3:
    filename = filename + '_' + AXIS[data_num[-1, -5]] + '_' + PHASE[AXIS[data_num[-1, -5]]][data_num[-1, -4]]
elif data.shape[0]==1:
    print('no data acquired')
else:
    print('problem with data size')
    
np.savetxt((filename + '.txt'), (data), delimiter=",", fmt="%s")
# np.savetxt('test_skelall_eul.txt', (skel_eul_all), delimiter=",", fmt="%s")
# np.savetxt('test_boneall.txt', (motive_data), delimiter=",", fmt="%s")
# np.savetxt('test.txt', (motive_data), delimiter=",", fmt="%s")
# np.savetxt('test_1.txt', (motive_data_full), delimiter=",", fmt="%s")

os.chdir(home_fol)

end = datetime.now()
print('total time = ', end - start)

data

total time =  0:03:34.334487


array([['ID_0', 'pos_x_0', 'pos_y_0', ..., 'is_input_not_zero',
        'instance', 'loop counter'],
       ['1.0', '0.7789430618286133', '0.9392685294151306', ..., '0.0',
        '0.0', '1.0'],
       ['1.0', '0.7789430618286133', '0.9392685294151306', ..., '0.0',
        '0.0', '2.0'],
       ...,
       ['1.0', '0.7789430618286133', '0.9392685294151306', ..., '1.0',
        '0.0', '7317.0'],
       ['1.0', '0.7789430618286133', '0.9392685294151306', ..., '1.0',
        '0.0', '7318.0'],
       ['1.0', '0.7789430618286133', '0.9392685294151306', ..., '1.0',
        '0.0', '7319.0']], dtype='<U32')

In [97]:
data_num.shape

(6655, 262)

In [99]:
data_row.shape

(1, 233)

In [52]:
data_num

array([[1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        0.00000000e+00, 0.00000000e+00, 2.00000000e+00],
       [1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        0.00000000e+00, 0.00000000e+00, 9.30000000e+01],
       [1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        0.00000000e+00, 0.00000000e+00, 1.42000000e+02],
       ...,
       [1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        1.00000000e+00, 0.00000000e+00, 1.30300000e+03],
       [1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        1.00000000e+00, 0.00000000e+00, 1.33300000e+03],
       [1.00000000e+00, 7.78943062e-01, 9.39268529e-01, ...,
        1.00000000e+00, 0.00000000e+00, 1.36100000e+03]])

In [94]:
# close unity write socket
Read_unity_query.socket.close()

# close unity control read socket
Read_unity_control.socket.close()

# close unity info read socket
Read_unity_info.socket.close()

# close motive read socket
Read_motive_sk.socket.close()

In [ ]:
filename

In [100]:
pd.read_csv(foldername + '\\' + filename + '.txt')

ID_0   pos_x_0   pos_y_0   pos_z_0  quat_x_0  quat_y_0  quat_z_0  \
0      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
1      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
2      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
3      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
4      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
5      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
7      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
8      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
9      1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
10     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
11     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
12     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
13     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
14     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
15     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
16     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
17     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
18     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
19     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
20     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
21     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
22     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
23     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
24     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
25     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
26     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
27     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
28     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
29     1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
...    ...       ...       ...       ...       ...       ...       ...   
6625   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6626   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6627   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6628   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6629   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6630   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6631   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6632   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6633   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6634   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6635   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6636   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6637   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6638   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6639   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6640   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6641   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6642   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6643   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6644   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6645   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6646   1.0  0.778943  0.939269 -4.617087  0.380024  0.093457  0.917376   
6647   1.0